# Agrupando letras de músicas de Rock

Aluno: Mateus Cavalcante de Almeida Farias Aires

Letras de músicas segundo o vagalume.com.br, coletadas por Anderson Neisse e [disponíveis no kaggle](https://www.kaggle.com/neisse/scrapped-lyrics-from-6-genres/data).

Os dados originais foram tratados para diminuir duplicações e diminuir o tamanho do arquivo. Os resultados (e outros recortes dos dados de letras) estão [nesse repo](https://github.com/nazareno/palavras-nas-letras).

In [1]:
import pandas as pd
import numpy as np
import altair as alt

In [2]:
from sklearn import preprocessing, decomposition, model_selection, metrics, pipeline
from sklearn.cluster import KMeans
from sklearn.feature_extraction.text import TfidfVectorizer
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
import re

[nltk_data] Downloading package stopwords to /home/mateus/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
rock_lyrics = pd.read_csv('https://raw.githubusercontent.com/nazareno/palavras-nas-letras/master/letras-ptbr-rock-grande.csv')

#### Observações iniciais
Vamos começar realizando algumas observações superficiais do Dataframe, a partir dos métodos sample(), info() e value_counts() de artistas.

In [4]:
rock_lyrics.sample(10)

SName  \
160                                   Declare Guerra   
1523                              Só Pelo Bem Querer   
1002                                           Festa   
4500                                     Ah! Ah! Ah!   
484   Biquini de Bolinha Amarelinha Tão Pequenininho   
3544                    As Melhores Putas do Alabama   
7552                                      De Repente   
563                                           Abismo   
6692                            Esse Tal de Vagalume   
811                              Parei Na Contra Mão   

                                                  Lyric            Artist  \
160   Vivendo em tempo fechado. Correndo atrás de ab...    Barão Vermelho   
1523  Sinto pressa em imaginar uma solução. para um ...        Detonautas   
1002  Festa - Charlie Brown Jr. Eu não agüento mais....  Charlie Brown Jr   
4500  Eu gosto é de rir, gargalhar me faz tão bem.. ...                PG   
484   Ana Maria entrou na cabine. E foi vestir um bi...             Blitz   
3544  As melhores putas do Alabama. E uma boa garraf...           Matanza   
7552  Olhei. Não vi ela há muito tempo. Há quanto te...             Skank   
563   A noite me leva pra rua. Promete o que eu quer...   Capital Inicial   
6692  Você não viu esse tal de vagalume. Você não vi...          Ventania   
811   Vinha voando no meu carro. Quando vi pela fren...      Cássia Eller   

      Songs  Popularity Genre  \
160     160         3.8  Rock   
1523    120         2.0  Rock   
1002    208        25.7  Rock   
4500    111         1.1  Rock   
484      57         1.3  Rock   
3544     95         1.3  Rock   
7552    139        12.3  Rock   
563     196         8.1  Rock   
6692     35         1.3  Rock   
811     141         7.5  Rock   

                                                 Genres  
160   Rock; Pop/Rock; MPB; Romântico; Rock Alternati...  
1523                                               Rock  
1002  Pop/Rock; Rap; Rock; Reggae; Rock Alternativo;...  
4500  Rock; Gospel/Religioso; Pop/Rock; Funk; Clássi...  
484   Pop/Rock; Pop; Rock; New Wave; Hip Hop; Forró;...  
3544  Hardcore; Rock; Hard Rock; Heavy Metal; Countr...  
7552  Pop/Rock; Rock; Pop; Rock Alternativo; MPB; Ro...  
563   Pop/Rock; Rock; Rock Alternativo; Punk Rock; M...  
6692  Reggae; Rock; Rock Alternativo; Ska; Reggaeton...  
811   Rock; MPB; Pop/Rock; Pop; Romântico; Samba; Co...

In [5]:
rock_lyrics.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7680 entries, 0 to 7679
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   SName       7680 non-null   object 
 1   Lyric       7680 non-null   object 
 2   Artist      7680 non-null   object 
 3   Songs       7680 non-null   int64  
 4   Popularity  7680 non-null   float64
 5   Genre       7680 non-null   object 
 6   Genres      7680 non-null   object 
dtypes: float64(1), int64(1), object(5)
memory usage: 420.1+ KB


In [6]:
rock_lyrics['Artist'].value_counts()[0:20]

Lulu Santos                462
Engenheiros do Hawaii      402
Jota Quest                 296
Skank                      290
Rita Lee                   282
Erasmo Carlos              236
Cássia Eller               226
Titãs                      209
Charlie Brown Jr           198
Raul Seixas                196
Capital Inicial            195
Biquini Cavadão            184
Os Paralamas do Sucesso    181
Barão Vermelho             164
Velhas Virgens             156
Fresno                     153
Blitz                      150
Pato Fu                    146
Ira!                       142
Rosa de Saron              137
Name: Artist, dtype: int64

#### Pré-processamento
Faremos o pré-processamento dos textos das letras a partir da exclusão de caracteres especiais

In [7]:
stop_words = set(stopwords.words("portuguese"))
print(len(stop_words))

204


In [8]:
rock_lyrics_c = []
rock_songs_titles = []
rock_titles_lyrics = []

for i in range(len(rock_lyrics.Lyric)):
    lyric = rock_lyrics['Lyric'][i]
    title = rock_lyrics['SName'][i]

    #remove special characters and digits
    lyric  = re.sub("(\\d|\\W)+|\w*\d\w*"," ",lyric )
    lyric = ' '.join(s for s in lyric.split() if (not any(c.isdigit() for c in s)) and len(s) > 2)
    rock_lyrics_c.append(lyric)
    rock_songs_titles.append(title)
    rock_titles_lyrics.append("{title} {lyric}".format(title = title, lyric = lyric))

rock_titles_lyrics[5:7]

['Meu Caminho Saudade Espero que logo logo vai passar Vontade Hoje quero matar com você Sempre que puder voltarei aqui Sempre que puder quero ver sorrir Felicidade vale tiver alguém pra dividir vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração Não quero estar sozinho vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração levo comigo aprendi usar solidão vivo bem comigo mesmo então Respeito com liberdade Onde estiver seja bem vinda agora você quiser Sempre que puder voltarei aqui Sempre que puder quero ver sorrir Felicidade vale tiver alguém pra dividir vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração Não quero estar sozinho vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração levo comigo vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração Não quero estar sozinho vou levar pra ver sol pra ver mar Andar m

#### Criando vetores TF-IDF

In [9]:
#TF-IDF vectorizer
tfv_lyrics = TfidfVectorizer(
        min_df = 10,
        max_df = 0.5,
        max_features = None,
        stop_words = stop_words, 
        ngram_range = (1,3)
  )

tfv_titles = TfidfVectorizer(
        min_df = 10,
        max_df = 0.5,
        max_features = None,
        stop_words = stop_words, 
        ngram_range = (1,3)
  )

tfv_titles_lyrics = TfidfVectorizer(
        min_df = 10,
        max_df = 0.5,
        max_features = None,
        stop_words = stop_words, 
        ngram_range = (1,3)
  )



#transform
vec_lyrics = tfv_lyrics.fit_transform(rock_lyrics_c)
vec_titles = tfv_titles.fit_transform(rock_songs_titles)
vec_titles_lyrics = tfv_titles_lyrics.fit_transform(rock_titles_lyrics)

#returns a list of words.
lyrics_words = tfv_lyrics.get_feature_names()
titles_words = tfv_titles.get_feature_names()
tl_words = tfv_titles_lyrics.get_feature_names()

print(len(lyrics_words), len(titles_words), len(tl_words))

8525 226 8632


/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


### Escolhendo o valor de K
Para escolher o valor de K, usaremos o método do 'cotovelo': escolheremos o valor a partir do qual não haverá ganho substancial de coesão dos grupos com um valor de K maior.


In [10]:
from sklearn.cluster import MiniBatchKMeans

# k é o número de clusters, e ssd é nosso parâmetro de 'qualidade', calculado a partir das somas das distâncias quadráticas entre cada ponto e o centroide de seu respectivo grupo
# Considerando que os dados
qualidade_lyrics = pd.DataFrame(columns = ['k', 'ssd'])
qualidade_titles = pd.DataFrame(columns = ['k', 'ssd'])
qualidade_tl = pd.DataFrame(columns = ['k', 'ssd'])

for k in range(1, 17):
  kmeans_l = MiniBatchKMeans(n_clusters=k, init_size=1024, batch_size=2048, random_state=20)
  kmeans_l.fit(vec_lyrics)
  qualidade_lyrics = qualidade_lyrics.append({'k': k, 'ssd' : kmeans_l.inertia_}, ignore_index=True)

  kmeans_t = KMeans(n_clusters=k, random_state=0)
  kmeans_t.fit(vec_titles)
  qualidade_titles = qualidade_titles.append({'k': k, 'ssd' : kmeans_t.inertia_}, ignore_index=True)

  kmeans_tl = MiniBatchKMeans(n_clusters=k, init_size=1024, batch_size=2048, random_state=20)
  kmeans_tl.fit(vec_titles_lyrics)
  qualidade_tl = qualidade_tl.append({'k': k, 'ssd' : kmeans_tl.inertia_}, ignore_index=True)


In [11]:
alt.Chart(qualidade_lyrics).mark_line(
    point=True
).encode(
    x = 'k',
    y = alt.Y('ssd', scale = alt.Scale(zero=False))
)

alt.Chart(...)

In [12]:
alt.Chart(qualidade_titles).mark_line(
    point=True
).encode(
    x = 'k',
    y = alt.Y('ssd', scale = alt.Scale(zero=False))
)

alt.Chart(...)

In [13]:
alt.Chart(qualidade_tl).mark_line(
    point=True
).encode(
    x = 'k',
    y = alt.Y('ssd', scale = alt.Scale(zero=False))
)

alt.Chart(...)

O valor de K escolhido para o agrupamento dos conjuntos de dados será 8.

### Agrupando com o valor de K escolhido

In [14]:
kmeans_l = MiniBatchKMeans(n_clusters=8, init_size=1024, batch_size=2048, random_state=20)
kmeans_l.fit(vec_lyrics)
labels_l = kmeans_l.predict(vec_lyrics)

lyrics_ag = rock_lyrics.assign(grupo = labels_l)


lyrics_ag.sample(10)


SName  \
6976                     9051   
860                 Brasil Tv   
1650        Esportes Radicais   
3729        Zerar E Recomeçar   
4868         Pequena Raimunda   
5284  Departamento de Criação   
6904         Só Se For A Dois   
4464               Spectreman   
6346          Tudo Vai Passar   
113          Meus Bons Amigos   

                                                  Lyric  \
6976  Não quero jogar fora o pouco tempo que nos res...   
860   Aqui nesta esquina do Brasil. Eu te peço um po...   
1650  Preso no trânsito. De astros imóveis. Faço as ...   
3729  Eu estou aqui,. Então diga pra mim. O que eu n...   
4868  Olhe só Rodrigo,. Rodolfo, Fred e Canisso. Fei...   
5284  Quem vive pra servir assim. Não serve pra vive...   
6904  Aos gurus da índia. aos judeus da palestina. a...   
4464  (Planeta: a Terra. Cidade: Tóquio.. Como todas...   
6346  Estranhei tua visita,. Você estava tão distant...   
113   Meus bons amigos, onde estão. Notícias de todo...   

                     Artist  Songs  Popularity Genre  \
6976  Engenheiros do Hawaii    193        11.9  Rock   
860                  Cazuza    123         9.6  Rock   
1650  Engenheiros do Hawaii    193        11.9  Rock   
3729                Nx Zero    122         3.4  Rock   
4868              Raimundos    121         4.2  Rock   
5284               Rita Lee    297         7.6  Rock   
6904           Cássia Eller    141         7.5  Rock   
4464          Pedra Letícia     39         1.1  Rock   
6346                  Titãs    228         8.9  Rock   
113          Barão Vermelho    160         3.8  Rock   

                                                 Genres  grupo  
6976  Pop/Rock; Rock; Pop; Rock Alternativo; MPB; Se...      3  
860   Pop/Rock; MPB; Rock; Romântico; Rock Alternati...      1  
1650  Pop/Rock; Rock; Pop; Rock Alternativo; MPB; Se...      1  
3729                                               Rock      7  
4868  Punk Rock; Hardcore; Rock; Pop/Rock; Hard Rock...      5  
5284  Rock; Pop/Rock; MPB; Rock Alternativo; Jovem G...      5  
6904  Rock; MPB; Pop/Rock; Pop; Romântico; Samba; Co...      0  
4464  Pop/Rock; Rock; Pop; Rock Alternativo; Hard Ro...      5  
6346  Pop/Rock; Rock; Hard Rock; MPB; Pop; World Mus...      3  
113   Rock; Pop/Rock; MPB; Romântico; Rock Alternati...      0

In [44]:
kmeans_t =  KMeans(n_clusters=4, random_state=0)
kmeans_t.fit(vec_titles)
labels_t = kmeans_t.predict(vec_titles)

titles_ag = rock_lyrics.assign(grupo = labels_t)


titles_ag.sample(10)

SName  \
5056             Rockixe   
4021            Lágrimas   
2614      Libere A Mente   
165       Eclipse Oculto   
1949    Os Sete Gatinhos   
2730    Quase Sem Querer   
3434  Como Tudo Deve Ser   
4086              Óculos   
2698            Telefone   
2848          Fotografia   

                                                                                                    Lyric  \
5056  Vê se me entende, olha o meu sapato novo. Minha calça colorida o meu novo way of life. Estou tão...   
4021  Lembra da inocência, que aflorava, a alma pura. Indo livre como se deve, sem dever e nem correr....   
2614  Libere a mente, hoje tem baile!. Libere a mente, hoje tem baile!. Libere a mente, hoje tem baile...   
165   Nosso amor não deu certo. Gargalhadas e lágrimas. De perto fomos quase nada. Tipo de amor que nã...   
1949  Almas enganadas, sonhos de isopor. Carnes mal amadas. Simulando sensações de amor. E de cor .......   
2730  Tenho andado distraído. Impaciente e indeciso. E ainda estou confuso. Só que agora é diferente. ...   
3434  Sempre os mesmos velhos erros. Todo dia fazem me lembrar. Quando o peso cai sobre mim. Vai ficar...   
4086  Se as meninas do Leblon. Não olham mais pra mim.. Eu uso óculos. E volta e meia. Eu entro com me...   
2698  O telefone toca e o meu peito vibra. Tipo de coisa que só acontece quando cê me liga (x2). E eu ...   
2848  Fotografia. (Leoni/Leo Jaime). . Hoje o mar faz onda feito criança. No balanço calmo a gente des...   

                       Artist  Songs  Popularity Genre  \
5056              Raul Seixas    215        14.0  Rock   
4021               Oficina G3    134         2.3  Rock   
2614               Jota Quest    154        13.3  Rock   
165            Barão Vermelho    160         3.8  Rock   
1949            Erasmo Carlos    225         2.3  Rock   
2730            Legião Urbana    118        27.7  Rock   
3434                    Malta     43         1.4  Rock   
4086  Os Paralamas do Sucesso    224         7.0  Rock   
2698                    Lagum     17         3.8  Rock   
2848                    Leoni     91         2.0  Rock   

                                                                                                   Genres  \
5056  Rock; Pop/Rock; MPB; Rock Alternativo; Clássico; Rockabilly; Psicodelia; Folk; Country; Blues; C...   
4021  Hard Rock; Pop/Rock; Rock; Gospel/Religioso; Heavy Metal; Hardcore; Progressivo; Piano Rock; Roc...   
2614  Pop/Rock; Pop; Rock; Romântico; Funk; Black Music; Trilha Sonora; Soul Music; Hip Hop; Rock Alte...   
165   Rock; Pop/Rock; MPB; Romântico; Rock Alternativo; Forró; Trance; Trilha Sonora; K-Pop/K-Rock; In...   
1949  Rock; Jovem Guarda; Romântico; MPB; Soul Music; Psicodelia; Samba; Dance; Classic Rock; Fado; Fo...   
2730  Rock; Pop/Rock; MPB; Punk Rock; Pós-Punk; Black Music; Clássico; Funk; Dance; Grunge; Funk Cario...   
3434  Romântico; Rock; Rock Alternativo; Pop/Rock; Hard Rock; Sertanejo; Funk; Heavy Metal; Pop; Hardc...   
4086                                                                                                 Rock   
2698                                                                           Rock; Surf Music; Pop/Rock   
2848                                                          MPB; Rock; Romântico; Pop/Rock; Pop; Reggae   

      grupo  
5056      0  
4021      0  
2614      0  
165       0  
1949      0  
2730      0  
3434      0  
4086      0  
2698      0  
2848      0

In [16]:
kmeans_tl = MiniBatchKMeans(n_clusters=8, init_size=1024, batch_size=2048, random_state=20)
kmeans_tl.fit(vec_titles_lyrics)
labels_tl = kmeans_tl.predict(vec_titles_lyrics)

tl_ag = rock_lyrics.assign(grupo = labels_tl)


tl_ag.sample(10)

SName  \
3030   Os Tipos Que Eu Não Fui   
5423              Sassaricando   
575                Aua-aua !!!   
7555  É Uma Partida De Futebol   
5825                  Silêncio   
2044                     Maria   
4629               10 de Junho   
4540                  Gratidão   
1836          De Noite Na Cama   
4207                   Pólvora   

                                                  Lyric  \
3030  Nem vem me inventar. Eu nunca fui assim. Eu já...   
5423  Sassaricando. Todo mundo leva a vida no arame....   
575   Se eu não tenho mar, nem um puto. Nem alguém p...   
7555  Bola na trave não altera o placar. Bola na áre...   
5825  Só assim pra saber. Sem ninguém sem você. A ve...   
2044  Maria quando eu te vi. A minha vida te escolhe...   
4629  Um dia passei por uma rua escura, cheia de car...   
4540  MEU REFÚGIO E DESCANSO. GRATO SOU, PELA VIDA Q...   
1836  De noite, na cama, eu fico pensando. Se você m...   
4207  As teorias que explicam o universo. Os versos ...   

                       Artist  Songs  Popularity Genre  \
3030                    Lobão    112         1.3  Rock   
5423                 Rita Lee    297         7.6  Rock   
575           Capital Inicial    196         8.1  Rock   
7555                    Skank    139        12.3  Rock   
5825                  Scalene     73         0.8  Rock   
2044                  Esteban     55         0.9  Rock   
4629                    Pitty     98         8.1  Rock   
4540                       PG    111         1.1  Rock   
1836            Erasmo Carlos    225         2.3  Rock   
4207  Os Paralamas do Sucesso    224         7.0  Rock   

                                                 Genres  grupo  
3030  Rock; MPB; Rock Alternativo; Punk Rock; Psicod...      4  
5423  Rock; Pop/Rock; MPB; Rock Alternativo; Jovem G...      6  
575   Pop/Rock; Rock; Rock Alternativo; Punk Rock; M...      4  
7555  Pop/Rock; Rock; Pop; Rock Alternativo; MPB; Ro...      6  
5825  Rock Alternativo; Rock; Pop/Rock; Hardcore; Pu...      3  
2044  Rock; Emocore; Blues; Indie; Rock Alternativo;...      5  
4629  Rock Alternativo; Rock; Pop/Rock; Punk Rock; H...      1  
4540  Rock; Gospel/Religioso; Pop/Rock; Funk; Clássi...      7  
1836  Rock; Jovem Guarda; Romântico; MPB; Soul Music...      1  
4207                                               Rock      5

### Interpretando os grupos
Interpretaremos o grupo a partir da observação das palavras mais comuns de cada grupo, dos artistas mais presentes em cada grupo e da visualização dos grupos, com uma técnica de redução de dimensionalidade.

Começaremos a análise com as letras das músicas

In [17]:
# Vamos olhar a quantidade de músicas em cada grupo
lyrics_ag['grupo'].value_counts()


5    2725
1     897
3     894
7     755
0     744
6     708
2     674
4     283
Name: grupo, dtype: int64

In [18]:
# Olharemos, agora, as palavras mais comuns em cada grupo
lyrics_common_words = kmeans_l.cluster_centers_.argsort()[:,-1:-15:-1]
for num, centroid in enumerate(lyrics_common_words):
    print(str(num) + ' : ' + ', '.join(lyrics_words[word] for word in centroid))



0 : amor, mim, coração, tudo, ser, vem, dor, vou, vai, vida, amar, bem, assim, sei
1 : gente, sempre, sol, vem, quer, faz, nada, tudo, dia, vida, luz, ninguém, tempo, noite
2 : vamos, mundo, hoje, todo, dia, todo mundo, tudo, todos, vai, ser, vida, gente, tempo, amo
3 : vou, vai, tudo, sei, mim, aqui, tempo, agora, onde, ser, ficar, dia, vez, ver
4 : vida, toda, vida vida, tudo, gente, viver, ter, ser, tempo, mundo, vai, sinto, dia, agora
5 : vai, bem, tão, tudo, ser, mim, deus, aqui, ninguém, assim, faz, pode, tempo, mal
6 : quero, ser, ver, vai, tudo, vou, mim, sei, bem, quero ver, sempre, nada, quero ser, nunca
7 : sei, dizer, nada, coisas, tudo, mim, tempo, preciso, assim, viver, aqui, ser, agora, nunca


In [38]:
pd.options.display.max_colwidth = 100
lyrics_ag.query('grupo == 7')[['SName', 'Lyric', 'Artist']].sample(10)

SName  \
4285             1 de vocês   
6850                 Espaço   
3156           Samba a Dois   
437      Um Minuto Com Você   
4482            Tempo Certo   
2465           Estrategista   
2542  Aisumasen (I'm Sorry)   
6217               Diversão   
2563                A Gente   
6980               A Fábula   

                                                                                                    Lyric  \
4285  1,2,3 vai lá um de vocês. Diz o que é preciso. Com sinceridade. D. Ruga na mão é linha, na testa...   
6850  Quarto de não dormir. Sala de não estar. Porta de não abrir. Pátio de sufocar. Carta no corredor...   
3156  Quem se atreve a me dizer. Do que é feito o samba. Quem se atreve a me dizer. (2x). Não, eu não ...   
437   É hora de dizer adeus. Só mais um minuto com você. Onde encontrar no universo do seu olhar. Pala...   
4482  Sabe o que penso, conhece os meus caminhos. Sabe das dificuldades e o que estou sentindo. Na min...   
2465  Eu não sei por quanto tempo ainda vai durar. Esse temporal a me inundar. Mas sei bem o preço que...   
2542  TRADUÇÃO: DESCULPAS. Quando estou deprimido, verdadeiramente yin,. E não sei o que estou fazendo...   
6217  A vida até parece uma festa,. Em certas horas isso é o que nos resta.. Não se esquece o preço qu...   
2563  Não sei por que. Mas, às vezes, me sinto tão bem. Talvez nem perceba. Mas são coisas simples. Qu...   
6980  Era uma vez um planeta mecânico,. lógico, onde ninguem tinha dúvidas. havia nome pra tudo e para...   

                     Artist  
4285                Pato Fu  
6850           Cássia Eller  
3156           Los Hermanos  
437         Biquini Cavadão  
4482                     PG  
2465       Isabella Taviani  
2542            John Lennon  
6217                  Titãs  
2563             Jota Quest  
6980  Engenheiros do Hawaii

In [34]:
for g in range(0, 8):
  print('\n-----\nGRUPO {}:'.format(g))
  print(lyrics_ag.query('grupo ==  {}'.format(g))['Artist'].value_counts()[0:10])
  print('-----')


-----
GRUPO 0:
Jota Quest                 54
Lulu Santos                40
Erasmo Carlos              38
Skank                      36
Rita Lee                   33
Isabella Taviani           31
Los Hermanos               30
Rosa de Saron              29
Cássia Eller               28
Os Paralamas do Sucesso    26
Name: Artist, dtype: int64
-----

-----
GRUPO 1:
Engenheiros do Hawaii      90
Lulu Santos                66
Jota Quest                 52
Skank                      46
Rita Lee                   33
Os Paralamas do Sucesso    33
Capital Inicial            27
Erasmo Carlos              26
Velhas Virgens             26
Biquini Cavadão            25
Name: Artist, dtype: int64
-----

-----
GRUPO 2:
Engenheiros do Hawaii    68
Lulu Santos              50
Jota Quest               42
Capital Inicial          26
Legião Urbana            24
Blitz                    22
Charlie Brown Jr         22
Skank                    22
Barão Vermelho           20
Cássia Eller             20
Name: 

In [48]:
from sklearn.manifold import TSNE

lyrics_embedded = TSNE(n_components=2, verbose=1).fit_transform(vec_lyrics)

/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 7680 samples in 0.001s...
[t-SNE] Computed neighbors for 7680 samples in 2.276s...
[t-SNE] Computed conditional probabilities for sample 1000 / 7680
[t-SNE] Computed conditional probabilities for sample 2000 / 7680
[t-SNE] Computed conditional probabilities for sample 3000 / 7680
[t-SNE] Computed conditional probabilities for sample 4000 / 7680
[t-SNE] Computed conditional probabilities for sample 5000 / 7680
[t-SNE] Computed conditional probabilities for sample 6000 / 7680
[t-SNE] Computed conditional probabilities for sample 7000 / 7680
[t-SNE] Computed conditional probabilities for sample 7680 / 7680
[t-SNE] Mean sigma: 0.542048
[t-SNE] KL divergence after 250 iterations with early exaggeration: 128.586304
[t-SNE] KL divergence after 1000 iterations: 3.790422


In [60]:
lyrics_ag = lyrics_ag.assign(tsne1 = lyrics_embedded[:,0], tsne2 = lyrics_embedded[:,1])

alt.Chart(lyrics_ag.sample(1000)).mark_circle(
    opacity = .7,
    size = 30
).encode(
    x = 'tsne1',
    y = 'tsne2', 
    color = 'grupo:N',
    tooltip = ['Artist', 'SName']
).interactive()

alt.Chart(...)

#### Nomes de cada grupo:
Obs.: como rockeiro é romântico; amor, recíproco ou não, é um tema recorrente em todos os grupos. Essa será uma tentativa de identificá-los além desse tema:
* 0 -> grupo dos amantes (os que cantam sobre um amor ardente, que existe ou não existe mais).
* 1 -> grupo dos esperançosos e dos desesperançosos (pensamentos bons ou ruins sobre futuro).
* 2 -> grupo dos festeiros (muitas menções a festas, dias de semana e acordar sentindo algo de especial).
* 3 -> grupo dos "estou te esperando" (amores escondidos, ou amores passados que ainda perduram no coração de alguém).
* 4 -> grupo dos pensantes sobre a vida (muitas menções a vida e ao ato de viver).
* 5 -> grupo dos invocados (menções de inferno, sangue, alma, Deus e palavrões).
* 6 -> grupo dos emocionados (menções a se entregar por completado a alguém ou a Deus)
* 7 -> grupo dos revolucionários (menções a se revoltar contra o sistema)

Agora, faremos a análise a partir dos títulos das músicas

In [45]:
titles_ag['grupo'].value_counts()

0    7226
2     182
1     180
3      92
Name: grupo, dtype: int64

In [46]:
titles_common_words = kmeans_t.cluster_centers_.argsort()[:,-1:-15:-1]
for num, centroid in enumerate(titles_common_words):
    print(str(num) + ' : ' + ', '.join(titles_words[word] for word in centroid))

0 : tudo, part, vida, tempo, dia, sol, homem, vai, nada, coração, noite, vou, mim, quero
1 : amor, apenas, grande, maior, daqui, vida, todo, balada, quente, mim, canção, part, onde, paz
2 : pra, pra mim, mim, pra ser, ser, sempre, vou, ficar, projota, canção, daqui, onde, vida, frente
3 : mundo, todo mundo, todo, fim, outro, todas, dá, história, lua, novo, tão, sobre, vai, dois


In [49]:
pd.options.display.max_colwidth = 100
lyrics_ag.query('grupo == 2')[['SName', 'Lyric', 'Artist']].sample(10)

SName  \
5814                       Nós Maior Que Eles   
126                             Amor de Irmão   
3736  Abra A Felicidade (comercial Coca-Cola)   
3067                     Vamos Para O Espaço!   
1664                     Illex Paraguariensis   
6176                               Agonizando   
2638              Oxigênio (Part. Zé Ramalho)   
3286                              Hoje em Dia   
1600                                 A Perigo   
3446                        Mais do Que Ontem   

                                                                                                    Lyric  \
5814  Cada sorriso seu. Às custas de milhões. De pessoas indefesas. Confiando em vão. Em uma mudança v...   
126   Está chegando. Um novo tempo de paz. Junto com a chuva. Indo embora pro mar. E num improviso da ...   
3736  Alô, aumente o som!. Tem alguém aí me ouvindo?. Aham !. Um novo dia chegou.. E eu quero, pra com...   
3067  MAIS UMA VEZ. EU VI QUE ELA QUERIA. FICAR. MAS NÃO SABIA. POR ONDE COMEÇAR. A DAR SINAIS DE UMA ...   
1664  Hoje eu acordei mais cedo. Tomei sozinho o chimarrão. Procurei a noite na memória. Procurei em v...   
6176  Agonizando. Até o osso, até o fim. Até o fundo, até o final. Até rasgar, até bater. Até furar, a...   
2638  Mesmo com a fumaça. Dá para ver. A incessante sinfonia. Da floresta. Respirando pelo mundo. Vend...   
3286  O nosso amor virou notícia. Ganhou a capa do jornal. Depois quebrou a internet. Viralizou geral....   
1600  Planos de vôo. Tava tudo em cima: céu de brigadeiro sobre nós. Pane... pânico. Perdemos a altura...   
3446  Igual ou não ninguém ou todo mundo. Na contra mão cavando mais profundo. Não sei se sou mais cla...   

                     Artist  
5814                Scalene  
126          Barão Vermelho  
3736                Nx Zero  
3067                  Lobão  
1664  Engenheiros do Hawaii  
6176                  Titãs  
2638             Jota Quest  
3286            Lulu Santos  
1600  Engenheiros do Hawaii  
3446                  Malta

In [50]:
for g in range(0, 4):
  print('\n-----\nGRUPO {}:'.format(g))
  print(titles_ag.query('grupo ==  {}'.format(g))['Artist'].value_counts()[0:10])
  print('-----')


-----
GRUPO 0:
Lulu Santos              442
Engenheiros do Hawaii    378
Skank                    280
Rita Lee                 268
Jota Quest               260
Erasmo Carlos            225
Cássia Eller             214
Titãs                    193
Raul Seixas              186
Capital Inicial          185
Name: Artist, dtype: int64
-----

-----
GRUPO 1:
Lulu Santos                14
Leoni                      13
Blitz                      12
Jota Quest                 12
Barão Vermelho              9
Rita Lee                    9
PG                          8
Ira!                        7
Os Paralamas do Sucesso     6
Engenheiros do Hawaii       6
Name: Artist, dtype: int64
-----

-----
GRUPO 2:
Jota Quest               20
Engenheiros do Hawaii    16
Titãs                     9
Charlie Brown Jr          9
Aliados                   9
Biquini Cavadão           8
Nx Zero                   8
Pato Fu                   7
Velhas Virgens            6
Raul Seixas               6
Name: Artist, dt

In [51]:
from sklearn.manifold import TSNE

titles_embedded = TSNE(n_components=2, verbose=1).fit_transform(vec_titles)

/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 7680 samples in 0.000s...
[t-SNE] Computed neighbors for 7680 samples in 0.731s...
[t-SNE] Computed conditional probabilities for sample 1000 / 7680
[t-SNE] Computed conditional probabilities for sample 2000 / 7680
[t-SNE] Computed conditional probabilities for sample 3000 / 7680
[t-SNE] Computed conditional probabilities for sample 4000 / 7680
[t-SNE] Computed conditional probabilities for sample 5000 / 7680
[t-SNE] Computed conditional probabilities for sample 6000 / 7680
[t-SNE] Computed conditional probabilities for sample 7000 / 7680
[t-SNE] Computed conditional probabilities for sample 7680 / 7680
[t-SNE] Mean sigma: 0.000000
[t-SNE] KL divergence after 250 iterations with early exaggeration: 99.977097
[t-SNE] KL divergence after 1000 iterations: 2.367427


In [52]:
titles_ag = titles_ag.assign(tsne1 = titles_embedded[:,0], tsne2 = titles_embedded[:,1])

alt.Chart(titles_ag.sample(1000)).mark_circle(
    opacity = .7,
    size = 30
).encode(
    x = 'tsne1',
    y = 'tsne2', 
    color = 'grupo:N',
    tooltip = ['Artist', 'SName']
).interactive()

alt.Chart(...)

#### Nomeando os grupos
Obs.: Essa é uma tarefa difícil e subjetiva, porque um grupo possui a grande maioria das músicas. Eu diria que utilizar somente os títulos como parâmetro de agrupamento não é uma boa estratégia.
* 0 -> grupo dos diversos (todo tipo de coisa).
* 1 -> grupo dos amantes e apaixonados (muitas menções ao amor).
* 2 -> grupo das preposições (quase todas as músicas tem 'pra').
* 3 -> grupo dos pensantes sobre o mundo (muitas menções ao mundo).

Finalmente, faremos a análise a partir dos títulos concatenados com as letras

In [53]:
tl_ag['grupo'].value_counts()

5    2596
1    1161
3     926
2     794
0     707
4     659
6     603
7     234
Name: grupo, dtype: int64

In [54]:
tl_common_words = kmeans_tl.cluster_centers_.argsort()[:,-1:-15:-1]
for num, centroid in enumerate(tl_common_words):
    print(str(num) + ' : ' + ', '.join(tl_words[word] for word in centroid))


0 : amor, coração, tudo, vida, ser, vou, vem, amar, vai, dor, mim, mundo, dia, bem
1 : gente, sempre, vida, dia, sol, nada, faz, quer, tudo, noite, vem, tempo, medo, vai
2 : quero, vamos, ver, hoje, ser, dia, sei, tudo, vida, bem, vai, quero ver, amo, nada
3 : vou, vai, sei, tempo, tudo, aqui, agora, dizer, vez, onde, ficar, quero, ser, dia
4 : mim, tudo, pra mim, assim, sei, aqui, posso, vai, fim, ser, bem, vou, quero, sempre
5 : vai, tão, ser, bem, onde, tudo, aqui, vida, tempo, assim, nada, pode, sei, mal
6 : ninguém, todo, mundo, todo mundo, sabe, tudo, vai, dia, bem, vida, the, ser, gente, faz
7 : deus, senhor, jesus, rei, homem, cristo, coração, amor, aleluia, glória, vida, deus deus, viver, terra


In [60]:
pd.options.display.max_colwidth = 100
tl_ag.query('grupo == 4')[['SName', 'Lyric', 'Artist']].sample(10)

SName  \
2704                 Prá Lá de Bagdá   
6267                  Lilian, A Suja   
7473          Propriedade Particular   
1531                  Terra Estranha   
5748                       Bo Manera   
5608                   Metade de Mim   
5619                  No Meu Coração   
2944  Você Sabe O Que Eu Quero Dizer   
5487                   Segue A Linha   
2785               La Nuova Gioventú   

                                                                                                    Lyric  \
2704  Sempre me imaginei assim. Livre pra fazer o que eu tiver afim. "Vamo" lá, seja o que eu quiser. ...   
6267  Já faz muito tempo. Que eu sou afim de você. Mas você regulou. E eu não sei por que. Agora ouvin...   
7473  Queria que tu tivesse. Ciúmes de mim. Queria te ver armar uma cena assim. Xingando e quebrando c...   
1531  Eu sou assim. Igual a mim. Não há ninguém. Mas tudo bem, tudo bem. Mas tudo bem, tudo bem. Cara ...   
5748  Chorus:. Bem explicam bo manera. D´zem o ké, ke bo ta pensa. Bem tentam d´zem tudo k´em kré sabe...   
5608  Se um dia você me chamar, eu posso estar, eu posso estar. Em Qualquer lugar é meu lugar. Desde q...   
5619  Fazer, falar ou esperar vir de alguém. Algo que se faz compreender. Que amar é se dar pelo outro...   
2944  Solidão se serve a dois. E a minha dor fica pra depois. Porque o seu silêncio é quase sólido. Eu...   
5487  Rolando pedras e pedras. Velocidade do som, yo. Mudando tudo a sua volta. Melhorando sempre. O q...   
2785  Tudo que sei. É que você quis partir. Eu quis partir sem você. Tirar você de mim. Demorei para e...   

             Artist  
2704          Lagum  
6267          Titãs  
7473    Lulu Santos  
1531     Detonautas  
5748        Santana  
5608  Rosa de Saron  
5619  Rosa de Saron  
2944          Leoni  
5487          Rodox  
2785  Legião Urbana

In [90]:
for g in range(0, 7):
  print('\n-----\nGRUPO {}:'.format(g))
  print(tl_ag.query('grupo ==  {}'.format(g))['Artist'].value_counts()[0:10])
  print('-----')


-----
GRUPO 0:
Jota Quest                 56
Skank                      36
Lulu Santos                36
Erasmo Carlos              33
Rita Lee                   31
Cássia Eller               28
Isabella Taviani           27
Los Hermanos               26
Os Paralamas do Sucesso    26
Barão Vermelho             26
Name: Artist, dtype: int64
-----

-----
GRUPO 1:
Engenheiros do Hawaii      114
Lulu Santos                 94
Jota Quest                  64
Os Paralamas do Sucesso     45
Skank                       42
Biquini Cavadão             42
Rita Lee                    41
Capital Inicial             38
Erasmo Carlos               36
Raul Seixas                 35
Name: Artist, dtype: int64
-----

-----
GRUPO 2:
Lulu Santos              50
Cássia Eller             42
Engenheiros do Hawaii    34
Erasmo Carlos            27
Skank                    26
Charlie Brown Jr         26
Rita Lee                 24
Legião Urbana            23
Detonautas               22
Raul Seixas             

In [55]:
tl_embedded = TSNE(n_components=2, verbose=1).fit_transform(vec_titles_lyrics)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 7680 samples in 0.001s...
[t-SNE] Computed neighbors for 7680 samples in 2.264s...
[t-SNE] Computed conditional probabilities for sample 1000 / 7680
[t-SNE] Computed conditional probabilities for sample 2000 / 7680
[t-SNE] Computed conditional probabilities for sample 3000 / 7680
[t-SNE] Computed conditional probabilities for sample 4000 / 7680
[t-SNE] Computed conditional probabilities for sample 5000 / 7680
[t-SNE] Computed conditional probabilities for sample 6000 / 7680
[t-SNE] Computed conditional probabilities for sample 7000 / 7680
[t-SNE] Computed conditional probabilities for sample 7680 / 7680
[t-SNE] Mean sigma: 0.542122
[t-SNE] KL divergence after 250 iterations with early exaggeration: 136.320740
[t-SNE] KL divergence after 1000 iterations: 3.727776


In [56]:
tl_ag = tl_ag.assign(tsne1 = tl_embedded[:,0], tsne2 = tl_embedded[:,1])

alt.Chart(tl_ag.sample(1000)).mark_circle(
    opacity = .7,
    size = 30
).encode(
    x = 'tsne1',
    y = 'tsne2', 
    color = 'grupo:N',
    tooltip = ['Artist', 'SName']
).interactive()

alt.Chart(...)

#### Nomeando os grupos
Obs.: É interessante notar como algumas palavras no início de cada letra de música mudou de forma considerável o resultado final. Os primeiros grupos são bem parecidos com os formados quando o parâmetro era somente a letra, mas alguns mudaram. Não só isso: surgiu um novo grupo completamente diferente dos demais (grupo 7).
* 0 -> grupo dos amantes (os que cantam sobre um amor ardente, que existe ou não existe mais).
* 1 -> grupo dos esperançosos e dos desesperançosos (pensamentos bons ou ruins sobre futuro).
* 2 -> grupo dos festeiros (muitas menções a festas, dias de semana e acordar sentindo algo de especial).
* 3 -> grupo das idas e vindas (menções a ir e voltar).
* 4 -> grupo dos libertinos (menções à vaidade e sexualidade).
* 5 -> grupo dos diversos e selvagens (menções à selva, fogo em palha e nudez).
* 6 -> grupo de ninguém e de todo mundo (menções a ninguém e a todos nós).
* 7 -> grupo dos religiosos (menções a Deus, Jesus, glória e aleluia).